In [1]:
from IPython.display import Markdown as md
from IPython.display import display, HTML
import pandas as pd
import numpy as np
import ipywidgets as widgets
from pathlib import Path
from datetime import datetime
from recopytex import flat_df_students, pp_q_scores
from datetime import datetime


import chart_studio.plotly as py
import plotly.graph_objects as go
import plotly.figure_factory as ff

from plotly.offline import iplot, init_notebook_mode
init_notebook_mode()

In [2]:
tribe = "ES"
assessment = "ds2"
date = "14/10/19"
csv_file = Path(f"../{tribe}/191014_{assessment}.csv")

In [3]:
# Parameters
tribe = "2gt1"
assessment = "Dm2"
date = "27/03/23"
csv_file = "/home/lafrite/Cours/2022-2023/Notes/2gt1/230327_DM2.csv"


In [4]:
date = datetime.strptime(date, "%d/%m/%y")
output_path = Path(csv_file[:-4])
print(output_path)

/home/lafrite/Cours/2022-2023/Notes/2gt1/230327_DM2


In [5]:
if date is None:
    display(md(f"# {assessment} pour {tribe}"))
else:
    display(md(f"# {assessment} ({date:%y/%m/%d}) pour {tribe}"))

# Dm2 (23/03/27) pour 2gt1

In [6]:
stack_scores = pd.read_csv(csv_file, encoding="UTF8")
#comments = stack_scores.iloc[0]
#stack_scores.drop([0], inplace=True)
scores = flat_df_students(stack_scores).dropna(subset=["Score"])
scores = pp_q_scores(scores)
#scores.head()
#comments.drop()

In [7]:
exercises_scores = scores.groupby(["Exercice", "Eleve"]).agg({"Note": "sum", "Bareme": "sum"})

In [8]:
exercises_scores.head()

Note  Bareme
Exercice   Eleve                          
Exercice 1 ACHOUR Ilyes        1.0     3.0
           BELARBI Islem       3.0     3.0
           BEN ELALLID Hajar   3.0     3.0
           BISWAS Lina         2.0     3.0
           BOULAABA Rayan      2.0     3.0

In [9]:
assessment_scores = scores.groupby(["Eleve"]).agg({"Note": "sum", "Bareme": "sum"})

In [29]:
assessment_scores

Note  Bareme
Eleve                             
ACHOUR Ilyes          6.50    15.0
BELARBI Islem        12.67    15.0
BEN ELALLID Hajar     9.16    15.0
BISWAS Lina          10.00    15.0
BOULAABA Rayan       10.33    15.0
BREZUN Ines          10.83    15.0
BUGNON Enzo          10.50    15.0
CALLEWAERT Idaline   10.67    15.0
CATTIN Clément       12.00    15.0
DECOSTER Clément     13.50    15.0
DEHIMAT Launy        11.00    15.0
DUPONT Jessica       12.67    15.0
GASAN Jéssica        12.50    15.0
GEORGET Raphaël       9.84    15.0
HABBAZ Hajar         11.34    15.0
JACQUEMIER Samuel    12.50    15.0
JACQUIER Juliette     9.83    15.0
JOVIC Atanase         7.17    15.0
KASSI Cheïma         10.17    15.0
KICHENASSAMY Sanjay   8.83    15.0
LE VEUZIT Adrien     11.84    15.0
MANJALI Hiba         13.67    15.0
NEIVA Hugo           11.17    15.0
OLLIET Gioia          4.33    15.0
PERNOT Gabin         13.84    15.0
RIZZI Elisa          13.67    15.0
SIBABA Moaad          9.67    15.0
SOUJOL Damien        11.34    15.0
THORAL Fanny          8.67    15.0
TOURRETTE Elise      11.33    15.0
TROPHARDY Eline      12.34    15.0

In [11]:
domain_scores = scores.groupby(["Eleve", "Domaine"]).agg({"Note": "sum", "Bareme": "sum"})
domain_scores["Normalized"] = domain_scores["Note"] / domain_scores["Bareme"]

In [12]:
#domain_scores

In [13]:
competence_scores = scores.groupby(["Eleve", "Competence"]).agg({"Note": "sum", "Bareme": "sum"})
competence_scores["Normalized"] = competence_scores["Note"] / competence_scores["Bareme"]

In [14]:
competence_scores.tail()

Note  Bareme  Normalized
Eleve           Competence                           
TOURRETTE Elise Communiquer  0.33     1.0        0.33
                Représenter  3.00     4.5        0.67
TROPHARDY Eline Calculer     7.17     9.5        0.75
                Communiquer  0.67     1.0        0.67
                Représenter  4.50     4.5        1.00

### Bilans personnalisés

In [15]:
import pytex
#scores.head()

In [16]:
datas = {
    "assessment": {
        "name": assessment,
        "date": date
    },
    #"exercises": scores["Exercice"].unique(),
    #"questions": scores[["Exercice", 'Question', 'Competence', 'Domaine', 'Commentaire', 'Bareme', 'Est_nivele']],
    "eleves": {}
}
for e in scores["Eleve"].unique():
    edatas =  {
        "e": e,
        "assessment": assessment_scores.loc[e],
        "exercices": exercises_scores.xs(e, level="Eleve"),        "exercices": exercises_scores.xs(e, level="Eleve"),
        "domains": domain_scores.xs(e, level="Eleve"),
        "competences": competence_scores.xs(e, level="Eleve"),
        "exscores": {}
    }
    for i, ex in edatas["exercices"].iterrows():
        edatas["exscores"][i] = scores.loc[(scores.Exercice==i) & (scores.Eleve==e)]
    datas["eleves"][e] = edatas

In [17]:
score_template = r"""
\documentclass[a5paper,10pt]{article}
\usepackage{fullpage}
\usepackage{booktabs}
\usepackage{longtable}
\usepackage{tikz}
\usepackage{multicol}

\usepackage{geometry}
\geometry{left=10mm,right=10mm, top=10mm}

\renewcommand{\arraystretch}{1}
\setlength{\columnseprule}{0pt}

\pagestyle{empty}


\begin{document}


    \section*{\Var{assessment.name} \hfill \Var{e} \hfill \Var{sc.assessment.Note}/\Var{sc.assessment.Bareme}}
    %- for i,ex in sc.exercices.iterrows() 
        \subsection*{\Var{i}: \hfill \Var{ex.Note} / \Var{ex.Bareme}}
        \begin{center}
        \Var{sc.exscores[i].to_latex(index=False, columns=["Question", "Domaine", "Commentaire", "Note", "Bareme"])}
        \end{center}
    %- endfor
 
     \subsection*{Compétences}
     \begin{multicols}{2}
    %- for i,dom in sc.competences.iterrows()
        \noindent
        \Var{i} \hfill
        \begin{tikzpicture}[scale=0.7]
            \draw [](0,0) rectangle (3, 1);
            \draw [fill=black!20] (0, 0) rectangle (\Var{dom.Normalized*3}, 1);
        \end{tikzpicture}
        \hfill
        %\Var{dom.Normalized}
        
    %- endfor
    \end{multicols}

\end{document}
"""

In [18]:
tpl = pytex.texenv.from_string(score_template)

for e,sc in datas['eleves'].items():
    reportfilename = f"{date:%y%m%d}_{assessment}_{e}.tex"
    with open(output_path / reportfilename, "w") as f:
        f.write(tpl.render(sc=sc, e=e,**datas))
    print(f"Wrote {reportfilename}")
    pytex.pdflatex(reportfilename)

/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.

/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.

/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for 

Wrote 230327_Dm2_ACHOUR Ilyes.tex


/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.

/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.

/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for 

Wrote 230327_Dm2_BELARBI Islem.tex


/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.

/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.

/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for 

...

Wrote 230327_Dm2_THORAL Fanny.tex


/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.

/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.

/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for 

Wrote 230327_Dm2_TOURRETTE Elise.tex


/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.

/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.

/home/lafrite/.venv/enseignements/lib/python3.10/site-packages/jinja2/runtime.py:298: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for 

Wrote 230327_Dm2_TROPHARDY Eline.tex


## Envoie des bilans par mail

In [22]:
mailfrom = "benjamin.bertrand@ac-lyon.fr"
subject = f"Bian du devoir {assessment}"
message = """Bonsoir,
En pièce jointe, vous trouverez un document détaillant la note du devoir. 

Votre note est indiquée sur 15 dans la pièce jointe mais elle sera sur 14 sur Pronote par rapport à la dernière question sur l'écart type.


B.Bertrand
"""
print(subject)
print(message)

Bian du devoir Dm2
Bonsoir,
En pièce jointe, vous trouverez un document détaillant la note du devoir. 

Votre note est indiquée sur 15 dans la pièce jointe mais elle sera sur 14 sur Pronote par rapport à la dernière question sur l'écart type.


B.Bertrand



In [23]:
import smtplib
import os
import sys
from email.message import EmailMessage
import mimetypes
import time
import random

In [24]:
def build_msg(subj, to_addr, from_addr, body, att):
    msg = EmailMessage()
    msg["Subject"] = subj
    msg["To"] = to_addr
    #msg["To"] = "lafrite26@gmail.com"
    msg["From"] = from_addr
    msg.set_content(body)

    if att != []:
        ctype, encoding = mimetypes.guess_type(att)
        if ctype is None or encoding is not None:
            ctype = 'application/octet-stream'
        maintype, subtype = ctype.split('/', 1)
        with open(att, "rb") as f:
            msg.add_attachment(f.read(),
                maintype=maintype,
                subtype=subtype,
                filename=att.name)
    return msg


In [25]:
send = 1
fake = 0

In [26]:
if send:
    if fake:
        server = smtplib.SMTP("localhost", 8025)
        server.ehlo()
    else:
        server = smtplib.SMTP("smtps.ac-lyon.fr", 587)
        server.ehlo()
        server.starttls()
        server.ehlo()
        server.login("bbertrand", os.popen("pass Prof/Lyon/bbertrand").read()[:-1])   

In [27]:
try:
    eleves_data = pd.read_csv(f"../../{tribe}.csv")
except FileNotFoundError:
    try:
        eleves_data = pd.read_csv(f"../{tribe}.csv")
    except FileNotFoundError:
        eleves_data = pd.read_csv(f"{tribe}.csv")
eleves_data.fillna("", inplace=True)
#eleves_data

In [28]:
for e in eleves_data.iterrows():
    reportfilename = Path(f"{date:%y%m%d}_{assessment}_{e[1]['Nom']}.pdf")
    try:
        assert reportfilename.exists()
    except:
        print(f"Pas de rapport pour {e[1]['Nom']}")
    else:
        if e[1]["mail"] != "":
            if send:
                msg = build_msg(subject, e[1]["mail"], mailfrom, message, reportfilename)
                server.send_message(msg)
                print(f"\tBilan envoyé à {e[1]['Nom']}")
        else:
            print(f"Pas de mail pour {e[1]['Nom']}")
            

	Bilan envoyé à ACHOUR Ilyes
	Bilan envoyé à BELARBI Islem
	Bilan envoyé à BEN ELALLID Hajar
	Bilan envoyé à BISWAS Lina
	Bilan envoyé à BOULAABA Rayan
	Bilan envoyé à BREZUN Ines
	Bilan envoyé à BUGNON Enzo
	Bilan envoyé à CALLEWAERT Idaline
	Bilan envoyé à CATTIN Clément
Pas de rapport pour CHRISTMANN Nathan
	Bilan envoyé à DECOSTER Clément
	Bilan envoyé à DEHIMAT Launy
	Bilan envoyé à DUPONT Jessica
	Bilan envoyé à GASAN Jéssica
	Bilan envoyé à GEORGET Raphaël
	Bilan envoyé à HABBAZ Hajar
	Bilan envoyé à JACQUEMIER Samuel
	Bilan envoyé à JACQUIER Juliette
	Bilan envoyé à JOVIC Atanase
	Bilan envoyé à KASSI Cheïma
	Bilan envoyé à KICHENASSAMY Sanjay
	Bilan envoyé à LE VEUZIT Adrien
Pas de rapport pour LETIF Ilef
	Bilan envoyé à MANJALI Hiba
Pas de rapport pour MUTTONI Lou
	Bilan envoyé à NEIVA Hugo
	Bilan envoyé à OLLIET Gioia
	Bilan envoyé à PERNOT Gabin
	Bilan envoyé à RIZZI Elisa
Pas de rapport pour ROSTANT Emma
	Bilan envoyé à SIBABA Moaad
	Bilan envoyé à SOUJOL Damien
	Bilan env